In [1]:
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/home/mmkshira/spark-3.2.0-bin-hadoop2.7"

import findspark
findspark.init()


from pyspark.sql import SparkSession
import random

spark = SparkSession.builder.appName("YourTest").master("local[2]").config('spark.ui.port', random.randrange(4000,5000)).getOrCreate()

23/09/11 15:35:06 WARN Utils: Your hostname, scslt388 resolves to a loopback address: 127.0.1.1; using 10.32.10.73 instead (on interface wlp0s20f3)
23/09/11 15:35:06 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/09/11 15:35:07 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [2]:
from pyspark.sql.functions import explode
from pyspark.sql import functions as F

import pandas as pd
import plotly.express as px

In [27]:
training_data = spark.read.json("test.json")
training_data.createOrReplaceTempView("all_data")

In [28]:
all_data_sql = spark.sql("select * from all_data")

In [29]:
all_data_sql.select("references").show(5,False)

+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|references                                                                                                                                                                                                                                                                                      |
+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|null                                                                                                                          

In [7]:
testing2 = all_data_sql.select("id",explode("topics").alias("topic"))
testing2.createOrReplaceTempView('topics')


In [30]:
testing3=spark.sql(
    """select topic,   
    count(id) over (partition by topic) as total_papers_topic from topics"""
)
testing3.distinct().sort("total_papers_topic", ascending= False).show(10,False)


+----------------------------+------------------+
|topic                       |total_papers_topic|
+----------------------------+------------------+
|computer science            |10000             |
|artificial intelligence     |1540              |
|mechanical engineering      |981               |
|computer network            |622               |
|computer hardware           |584               |
|theoretical computer science|570               |
|computer vision             |479               |
|machine learning            |473               |
|electrical engineering      |382               |
|distributed computing       |327               |
+----------------------------+------------------+
only showing top 10 rows



### Distinct topics

In [31]:
def distinct_topics():
    return spark.sql("select distinct topic from topics")

In [32]:
# Top papers by topic
def top_papers(n=5):
    return main_topic_df.select("id","papertitle","authors","year","citationcount")\
        .orderBy("citationcount", ascending=False).limit(n)\
        .select("id","papertitle", explode("authors").alias("author"),"year","citationcount")\
        .select("id","papertitle","year","citationcount", F.col("author").getItem("name").alias("name"))\
        .groupBy(["id","papertitle","year","citationcount"]).agg(F.collect_list("name").alias("authors"))#.show()


In [33]:
# For timeline chart. number of citations. Each dot represents a paper
def timeline():
    df = main_topic_df.select("id","year","citationcount")\
        .orderBy("year").toPandas()
    fig = px.scatter(df,x="year",y="citationcount", opacity=0.5)
    return fig



In [34]:
#Top authors for a topic
def top_authors(n=5):
    global exploded_authors_topic
    exploded_authors_topic = main_topic_df.select("id",explode("authors").alias("author"),"citationcount")\
        .select("id", \
            F.col("author").getItem("country").alias("country"), \
            F.col("author").getItem("name").alias("name"), \
            F.col("author").getItem("id").alias("author_id"), \
            F.col("author").getItem("affiliation").alias("affiliation"), \
            "citationcount").cache()
    return exploded_authors_topic.select("name","author_id","citationcount")\
        .groupBy(["name","author_id"]).agg(F.sum("citationcount").alias("citationcount"))\
        .filter("name is not null")\
        .orderBy("citationcount", ascending=False).limit(n)

In [35]:
#Top institutions for a topic
def top_institutions(n=5):
    return exploded_authors_topic.select("id","affiliation","citationcount").distinct()\
        .groupBy(["affiliation"]).agg(F.sum("citationcount").alias("citationcount"))\
        .filter("affiliation is not null")\
        .orderBy("citationcount", ascending=False).limit(n)

In [36]:
def by_type():
    df = main_topic_df.select("id","type").distinct()\
        .filter("type is not null")\
        .groupBy("type").agg(F.count("id").alias("number of papers")).toPandas()
    return px.pie(df,names="type",values="number of papers")#.show()
     

In [37]:
# countries of institutions
def countries():
    df = exploded_authors_topic.select("id","country","citationcount").distinct()\
            .groupBy("country").agg(F.sum("citationcount").alias("citations")).toPandas()
    map_data = px.data.gapminder().query("year==2007")[["iso_alpha","country","continent"]]
    # df
    map_data = df[1:].merge(map_data,how="left").dropna()
    fig = px.choropleth(map_data, locations="iso_alpha",color="citations",
                     hover_name="country",color_continuous_scale=px.colors.sequential.Plasma)
    return fig#fig.show()


In [38]:
def main_topic(sel_topic, n_paper=5, n_author=5, n_institution=5):
    global main_topic_df
    main_topic_df = all_data_sql.filter(F.array_contains("topics",sel_topic)).select("id","type","papertitle","authors",F.year("year").alias("year"),"citationcount").cache()
    # Need to maintain this ordering to set global variables correctly
    top_author = top_authors(n_author)
    top_institutes = top_institutions(n_institution)
    top_paper = top_papers(n_paper)
    timeline_data = timeline()
    type_data = by_type()
    countries_data = countries()


    return top_author, top_institutes, top_paper, timeline_data, type_data, countries_data


top_author, top_institutes, top_paper, timeline_data, type_data, countries_data = main_topic("artificial intelligence")
top_author.show()
top_institutes.show()
top_paper.show()
timeline_data.show()
type_data.show()
countries_data.show()
    

+-----------------+----------+-------------+
|             name| author_id|citationcount|
+-----------------+----------+-------------+
|         jian sun|2200192130|        30269|
|diederik p kingma|2055604604|        28439|
|         jimmy ba|2097546270|        28430|
|       kaiming he|2164292938|        26087|
|    xiangyu zhang|2499063207|        24665|
+-----------------+----------+-------------+



+--------------------+-------------+
|         affiliation|citationcount|
+--------------------+-------------+
|Microsoft (United...|       103365|
|Carnegie Mellon U...|        45445|
|Massachusetts Ins...|        37494|
| Stanford University|        35257|
|Google (United St...|        32877|
+--------------------+-------------+

+----------+--------------------+----+-------------+--------------------+
|        id|          papertitle|year|citationcount|             authors|
+----------+--------------------+----+-------------+--------------------+
|2194775991|deep residual lea...|2016|        24222|[kaiming he, xian...|
|1522301498|adam a method for...|2014|        21088|[jimmy ba, dieder...|
|2964121744|adam a method for...|2015|         7296|[jimmy ba, dieder...|
|1803273808|the coding manual...|2009|         7295|    [johnny saldana]|
|1901129140|u net convolution...|2015|         7107|[thomas brox, phi...|
+----------+--------------------+----+-------------+--------------------+


In [39]:
# correlated topics with selected topics
sel_topic = "artificial intelligence"
testing2 = all_data_sql.filter(F.array_contains("topics",sel_topic)).select("id",explode("topics").alias("topic")).filter("topic != \'" +sel_topic+ "\'")
testing3 = testing2.groupBy("topic").count().sort("count",ascending=False).show()
testing2.show()


+--------------------+------+
|               topic| count|
+--------------------+------+
|    computer science|183686|
|     computer vision| 87246|
| pattern recognition| 47901|
|    machine learning| 47867|
|natural language ...| 19017|
|         data mining| 14556|
|artificial neural...| 11231|
|  feature extraction| 10842|
|  speech recognition| 10407|
|    image processing| 10324|
|               pixel|  9285|
|computer graphics...|  8581|
|        segmentation|  7620|
|           algorithm|  7576|
|support vector ma...|  7485|
|    cluster analysis|  6232|
|          classifier|  6033|
|  image segmentation|  5792|
|               robot|  5281|
|          robustness|  5159|
+--------------------+------+
only showing top 20 rows

+----------+--------------------+
|        id|               topic|
+----------+--------------------+
|2018731854|     computer vision|
|2018731854|     medical imaging|
|2018731854|            detector|
|2018731854|    computer science|
|2018731854|   3

In [40]:
# Authors for a given topic
sel_topic = "multimedia"
testing2 = all_data_sql.filter(F.array_contains("topics",sel_topic)).select("id",explode("authors").alias("authors"),"topics","type")
testing3 = testing2.select(testing2.id.alias("paper_id"), testing2.topics.alias("topics"), testing2.type.alias("type"), \
    F.col("authors").getItem("name").alias("name"), \
    F.col("authors").getItem("country").alias("country"), \
    F.col("authors").getItem("id").alias("author_id"), \
    F.col("authors").getItem("affiliation").alias("affiliation"), \
    )
testing4 = testing3.groupBy("country").count().sort("count",ascending=False) # country for a given topic
testing4 = testing3.groupBy("type").count().sort("count",ascending=False) # type for a given topic
testing4 = testing3.groupBy("affiliation").count().sort("count",ascending=False) # affiliation for a given topic
testing4 = testing3.groupBy("name").count().sort("count",ascending=False) # authors for a given topic
testing4.show(5,False)



+----------------------+-----+
|name                  |count|
+----------------------+-----+
|rob koper             |27   |
|susanne boll          |26   |
|mark billinghurst     |26   |
|abdulmotaleb el saddik|25   |
|adrian david cheok    |24   |
+----------------------+-----+
only showing top 5 rows



In [ ]:
# Calculate h-index


In [41]:
# Conferences for a given topic
sel_topic = "computer science"
testing2 = all_data_sql.filter(F.array_contains("topics",sel_topic)).select("id", \
    "confname","type", 'conferenceseriesid', 'confname', 'confplace', 'confseries', 'confseriesname') \
    .filter("confname is not null")


testing3 = testing2.groupBy("confseriesname").count().sort("count",ascending=False) # confseries for a given topic
testing3 = testing2.groupBy("confname").count().sort("count",ascending=False)
testing3.show()


+-------------+-----+
|     confname|count|
+-------------+-----+
|     icc 2015|  385|
|     icc 2009|  327|
|     icc 2012|  309|
|globecom 2010|  296|
|    embc 2011|  285|
|    cvpr 2018|  280|
|   wcica 2006|  278|
|    embc 2007|  265|
|    embc 2010|  263|
|     icc 2008|  262|
|    embc 2008|  260|
|    embc 2006|  256|
|    embc 2009|  251|
|    embc 2015|  244|
|    icip 2010|  239|
|    csse 2008|  226|
|     icc 2018|  226|
|    embc 2012|  220|
|  icassp 2018|  219|
|  icassp 2008|  214|
+-------------+-----+
only showing top 20 rows



In [42]:
# Citations
sel_topic = "multimedia"
testing2 = all_data_sql.filter(F.array_contains("topics",sel_topic)).select("id",explode("industrial_sectors").alias("industrial_sector")).filter("industrial_sectors is not null")
testing2.show(10,False)



+----------+----------------------+
|id        |industrial_sector     |
+----------+----------------------+
|2281235878|computing_and_it      |
|2281235878|technology            |
|2281235878|information_technology|
|2267368397|home_appliances       |
|2267368397|technology            |
|2267368397|electronics           |
|2311189127|electronics           |
|2311189127|technology            |
|2309667953|electronics           |
|2309667953|technology            |
+----------+----------------------+
only showing top 10 rows

